In [1]:
import warnings

warnings.filterwarnings('ignore')
warnings.simplefilter('ignore')

In [2]:
import pandas as pd
from IPython.display import HTML, display
# from transformers import GPT2Tokenizer

# tokenizer = GPT2Tokenizer.from_pretrained("gpt2")

In [3]:
df = pd.read_csv('story_datasets.csv')
# end_punct_ids = tokenizer("'' ? ! .")

# def shorten_to_1600_tokens(text):
#     tokens = tokenizer(text)['input_ids']
#     end = 1600

#     if len(tokens) > 1600:
#         for i in range(1600, 0, -1):
#             if i in end_punct_ids:
#                 end = i
#                 break

#     return tokenizer.decode(tokens[:end])
    
# df['ref'] = df['ref'].apply(shorten_to_1600_tokens)

# Which author is the better writer?

5 writers -- named **A, B, C, D, E** -- were given 6 writing prompts. For each prompt, they were asked to write a continuation of a few sentences. Carefully read each prompt and each writer's continuation of that prompt.

To begin, please enter your ReaderID below and click 'SEE TEXT' (scroll down to read all of the prompts). After reading, **please go back to Mechanical Turk and fill out the survey**.

In [6]:
output = []

for i in range(0, df['agent'].max() + 1):
    df_i = df[df['agent'] == i].drop(['agent'], axis=1).iloc[:6]
    df_i.index = list(range(1, len(df_i) + 1))

    df_i = df_i.rename(columns={
        "ref" : "E",
        "davinci-002": "D",
        "curie-001" : "C",
        "babbage-001" : "B",
        "ada-001" : "A",
    })[['prompt','A', 'B', 'C', 'D', 'E']]

    s = df_i.style
    s.set_properties(**{
        'text-align': 'left',
        'white-space': 'pre-wrap',
        'vertical-align': 'top',
        'width':'20em'
    }, overwrite=False)
    s.set_table_styles([
        {'selector': 'tbody th', 'props': 'position: sticky; left:0; background-color:white;'},
        {'selector': 'thead th', 'props': 'position: sticky; top:0; background-color:black; color: white; text-align:center'},
    ], overwrite=False)

    output.append(f"<div class='agent' id='agent{i}' style='display:none'>" + s.to_html() + "</div>")
    
    
display(HTML(
"""
<p class="jp-Cell">
Enter your ReaderID: <input id="myInput" type="number" value="0" min="%s" max="%s">
<button id="myBtn" onclick="makeVisible()">SEE TEXT</button>
</p>
""" % (df['agent'].min(), df['agent'].max())
))

display(HTML("<center><div style='max-height: 52vh; width: 100%; overflow-y: scroll;'>" + ''.join(output) + "</div></center>"))

display(HTML(
"""
<script>
var input = document.getElementById("myInput");
input.addEventListener("keypress", function(event) {
  if (event.key === "Enter") {
    event.preventDefault();
    document.getElementById("myBtn").click();
  }
});

function makeVisible() {
  var val = document.getElementById("myInput").value;  
  var elems = document.getElementsByClassName('agent');
  for (var i=0;i<elems.length;i+=1){
    elems[i].style.display = 'none';
  }

  document.getElementById("agent" + val).style.display = 'block';
}
</script>
""" 
))
